# The video tutorial of this notebook : 
# https://youtu.be/R2fEocf-MU8

 DeepFloyd IF

![](https://github.com/deep-floyd/IF/raw/main/pics/deepfloyd_if_scheme.jpg)

*Inspired by* [*Photorealistic Text-to-Image Diffusion Models with Deep Language Understanding*](https://arxiv.org/pdf/2205.11487.pdf)

### [[Github]](https://github.com/deep-floyd/IF) [[Model Card]](https://huggingface.co/DeepFloyd/IF-I-XL-v1.0)

## Installing:

In [ ]:
!pip install torch==1.13.1+cu117 torchvision==0.14.1+cu117 torchaudio==0.13.1 --extra-index-url https://download.pytorch.org/whl/cu117 > /dev/null
!pip install deepfloyd-if==1.0.2rc0 > /dev/null
!pip install xformers==0.0.16 > /dev/null
!pip install git+https://github.com/openai/CLIP.git --no-deps > /dev/null
!pip install -U accelerate~=0.18 > /dev/null
!pip install -U bitsandbytes~=0.38 > /dev/null
!pip install -U transformers~=4.28 > /dev/null
!pip install -U safetensors~=0.3 > /dev/null
!pip install -U sentencepiece~=0.1 > /dev/null

In [ ]:
!pip list | grep deepfloyd
!pip list | grep xformers
!pip list | grep torch
!pip list | grep transformers
!nvidia-smi

In [ ]:
import os
os.environ['FORCE_MEM_EFFICIENT_ATTN'] = "1"
import gc
import sys
import random

import torch
import numpy as np

from deepfloyd_if.modules import IFStageI, IFStageII, StableStageIII, T5Embedder

In [ ]:
hf_token = None # <---- put hf_token here only in private notebooks;
if hf_token is None:
    from huggingface_hub import login; login()  # put your hf_token in output of this cell if you want to share notebook in public;

In [ ]:
if_I = IFStageI('IF-I-XL-v1.0', device='cuda:1', hf_token=hf_token)
gc.collect();torch.cuda.empty_cache();

In [ ]:
t5 = T5Embedder(
    device='cuda:0',
    dir_or_name='DeepFloyd/IF-I-XL-v1.0',
    t5_model_kwargs={
        'load_in_8bit': True, 
#         'variant': "8bit", 
        'device_map': "sequential",
        "subfolder": "text_encoder",
    },
)
gc.collect();torch.cuda.empty_cache();

In [ ]:
%%time

if_II = IFStageII('IF-II-L-v1.0', device='cuda:1', hf_token=hf_token)

In [ ]:
%%time

if_III = StableStageIII('stable-diffusion-x4-upscaler', device='cuda:0')

In [ ]:
gc.collect();torch.cuda.empty_cache();

# use own prompts:

In [ ]:
#don't forget to run this cell too - this will be used to add naming to generated images to save and download all
# you only need to run this cell 1 time
imgnum=1000

In [ ]:
# dont forget to click play icon whenever you make a change to here write a prompt, it will iteratively genereate each prompt
prompts = [
   'aerial photo of a beach, the words "what if?" written in the sand',
    'an amazing intricate masterpiece space wallpaper that has the following word "SECourses"',
    'this the third prompt change as you wish add more prompts as you wish'
]

## generate:

In [ ]:
import random

pil_images_I = []
pil_images_II = []
pil_images_III = []

iteration_count=3

for i in range(iteration_count):
    for prompt in prompts:
        # t5:
        t5_embs = t5.get_text_embeddings([prompt])
        # seed = 1234
        # below will generate random seeds
        seed = random.randint(0, 999999)

        # if_I:
        stageI_generations, _meta = if_I.embeddings_to_image(
            t5_embs, seed=seed, batch_repeat=1,
            dynamic_thresholding_p=0.95,
            dynamic_thresholding_c=1.5,
            guidance_scale=7.0,
            sample_loop='ddpm',
            sample_timestep_respacing='150',
            image_size=64,
            aspect_ratio="1:1",
            progress=True,
        )
        pil_images_I += if_I.to_images(stageI_generations,disable_watermark=True)

        # if_II:
        stageII_generations, _meta = if_II.embeddings_to_image(
            stageI_generations,
            t5_embs, seed=seed, batch_repeat=1,
            dynamic_thresholding_p=0.95,
            dynamic_thresholding_c=1.0,
            aug_level=0.25,
            guidance_scale=4.0,
            image_scale=4.0,
            sample_loop='ddpm',
            sample_timestep_respacing='75',
            progress=True,
        )
        pil_images_II += if_II.to_images(stageII_generations,disable_watermark=True)

        gc.collect();torch.cuda.empty_cache();

        # if_III:
        if_III_kwargs = {}
        if_III_kwargs['prompt'] = [prompt]
        if_III_kwargs['low_res'] = stageII_generations
        if_III_kwargs['seed'] = seed
        if_III_kwargs['t5_embs'] = t5_embs
        stageIII_generations, _meta = if_III.embeddings_to_image(**if_III_kwargs)
        pil_images_III += if_III.to_images(stageIII_generations,disable_watermark=True)

        gc.collect();torch.cuda.empty_cache();


## show and save:

In [ ]:
# 
if_I.show(pil_images_I, size=3)
if_I.show(pil_images_II, size=6)

In [ ]:
localCounter=0
for perIter in range(iteration_count):
    for idx in range(len(prompts)):
        pil_img, prompt = pil_images_III[localCounter], prompts[idx]
        pil_img.save(f'{imgnum}_{idx}.png')
        if_I.show([pil_img],size=14)
        print(prompt, '\n'*3)
        imgnum=imgnum+1
        localCounter=localCounter+1

In [ ]:
# execute this cell to download all of the generated images as a single zip file

import zipfile
import os

# Define the name for the output zip file
zip_name = "working_directory.zip"

# Get the list of files in the working directory
file_list = os.listdir("/kaggle/working/")

# Create a zip file and add each file in the working directory to it
with zipfile.ZipFile(zip_name, "w", zipfile.ZIP_DEFLATED) as zip_file:
    for file in file_list:
        zip_file.write(os.path.join("/kaggle/working", file), file)

# Download the zip file
from IPython.display import FileLink
display(FileLink(zip_name))

In [ ]:
#this code will clear working directory - execute this if you want to delete generated images
import os
import shutil

dir_path = "/kaggle/working/"

# Check if directory exists
if os.path.exists(dir_path):
    # Iterate over all files and directories in the directory
    for root, dirs, files in os.walk(dir_path, topdown=False):
        for name in files:
            file_path = os.path.join(root, name)
            os.remove(file_path)  # Remove file
        for name in dirs:
            dir_path = os.path.join(root, name)
            shutil.rmtree(dir_path)  # Remove directory and its contents
else:
    print("Directory not found")
